# Initialization

In [55]:
import logging
import scipy
import sys
import sklearn.preprocessing
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error, ndcg_score
from surprise import Dataset, Reader
from surprise import SVD
from surprise import accuracy
from surprise import NormalPredictor
from scipy.sparse import csr_matrix
from implicit.als import AlternatingLeastSquares
from IPython.display import display
from sklearn.metrics.pairwise import cosine_similarity
from catboost import CatBoostClassifier, Pool
import random

In [2]:
%matplotlib inline
%config InlineBackend.figure_format = 'png'
%config InlineBackend.figure_format = 'retina'

# Загрузка данных

In [2]:
items = pd.read_parquet("items.parquet")
events = pd.read_parquet("events.parquet")

# Разбиение с учётом хронологии

Рекомендательные системы на практике работают с учётом хронологии. Поэтому поток событий для тренировки и валидации полезно делить на то, что уже случилось, и что ещё случится. Это позволяет проводить валидацию на тех же пользователях, на которых тренировались, но на их событиях в будущем.

# === Знакомство: "холодный" старт

In [3]:
# зададим точку разбиения
train_test_global_time_split_date = pd.to_datetime("2017-08-01").date()
train_test_global_time_split_idx = events["started_at"] < train_test_global_time_split_date

# разбиение на обучающую и тестовую выборки
events_train = events[train_test_global_time_split_idx]
events_test = events[~train_test_global_time_split_idx]

# количество пользователей в train и test
users_train = events_train["user_id"].drop_duplicates()
users_test = events_test["user_id"].drop_duplicates()

# количество пользователей, которые есть и в train, и в test
common_users = users_train[users_train.isin(users_test)]

print(len(users_train), len(users_test), len(common_users))

428220 123223 120858


In [4]:
# идентификация холодных пользователей
cold_users = users_test[~users_test.isin(users_train)]

print(len(cold_users))

2365


In [5]:
# зададим начальную дату для подсчета популярности
top_pop_start_date = pd.to_datetime("2015-01-01").date()

# подсчет популярности книг за последние несколько лет
item_popularity = events_train \
    .query("started_at >= @top_pop_start_date") \
    .groupby(["item_id"]).agg(users=("user_id", "nunique"), avg_rating=("rating", "mean")).reset_index()

# нормализация пользователей и среднего рейтинга
scaler = MinMaxScaler()
item_popularity[["users_norm", "avg_rating_norm"]] = scaler.fit_transform(
    item_popularity[["users", "avg_rating"]]
)

# вычисляем popularity_score, как скор популярности с учетом штрафа за низкий рейтинг
item_popularity["popularity_score"] = (
    item_popularity["users_norm"] * item_popularity["avg_rating_norm"]
)

# сортируем по убыванию popularity_score
item_popularity = item_popularity.sort_values(by="popularity_score", ascending=False).reset_index(drop=True)

# выбираем первые 100 айтемов со средней оценкой avg_rating не меньше 4
top_k_pop_items = item_popularity[item_popularity["avg_rating"] >= 4].head(100)

# выводим топ-100 популярных книг
print(top_k_pop_items[["item_id", "users", "avg_rating", "popularity_score"]])

      item_id  users  avg_rating  popularity_score
2    18007564  20207    4.321275          0.412333
3    18143977  19462    4.290669          0.393471
4           3  15139    4.706057          0.344702
5    16096824  16770    4.301014          0.340108
6       15881  13043    4.632447          0.291076
..        ...    ...         ...               ...
129   8490112   4792    4.080968          0.090694
130  18966819   4361    4.374914          0.090409
131      3636   4667    4.098564          0.088832
132  18293427   4674    4.092640          0.088795
133  26252859   4371    4.293068          0.088419

[100 rows x 4 columns]


In [6]:
# находим количество пользователей, оценивших книгу на первом месте
first_item_users_count = top_k_pop_items.iloc[0]['users']

print(first_item_users_count)

20207.0


In [7]:
# добавляем информацию о книгах
top_k_pop_items = top_k_pop_items.merge(
    items.set_index("item_id")[["author", "title", "genre_and_votes", "publication_year"]], on="item_id")

with pd.option_context('display.max_rows', 100):
    display(top_k_pop_items[["item_id", "author", "title", "publication_year", "users", "avg_rating", "popularity_score", "genre_and_votes"]])

item_id                                        author  \
0   18007564                                     Andy Weir   
1   18143977                                 Anthony Doerr   
2          3                   J.K. Rowling, Mary GrandPré   
3   16096824                                 Sarah J. Maas   
4      15881                   J.K. Rowling, Mary GrandPré   
5      38447                               Margaret Atwood   
6   11235712                                 Marissa Meyer   
7   17927395                                 Sarah J. Maas   
8          5                   J.K. Rowling, Mary GrandPré   
9   13206900                                 Marissa Meyer   
10  21853621                                Kristin Hannah   
11  18692431                      Nicola Yoon, David  Yoon   
12         6                   J.K. Rowling, Mary GrandPré   
13  16068905                                Rainbow Rowell   
14  23437156                                 Leigh Bardugo   
15   9969571                                  Ernest Cline   
16  17167166                                 Sarah J. Maas   
17  15745753                                Rainbow Rowell   
18  13206760                                 Marissa Meyer   
19  13206828                                 Marissa Meyer   
20  18006496                                 Sarah J. Maas   
21  20613470                                 Sarah J. Maas   
22      2657                                    Harper Lee   
23         2                   J.K. Rowling, Mary GrandPré   
24  18774964                 Fredrik Backman, Henning Koch   
25  18460392                                Jennifer Niven   
26   7896527                                 Sarah J. Maas   
27         1                                  J.K. Rowling   
28  20170404                         Emily St. John Mandel   
29    136251                                  J.K. Rowling   
30  16101128                                   Rick Yancey   
31      5470                    George Orwell, Erich Fromm   
32     19063                                  Markus Zusak   
33  23395680                    Amie Kaufman, Jay Kristoff   
34  25494343                               Cassandra Clare   
35  22055262                                   V.E. Schwab   
36  28260587                                 Sarah J. Maas   
37  23766634                                 Sarah J. Maas   
38  18798983                                  Renée Ahdieh   
39  27362503                                Colleen Hoover   
40  17675462                             Maggie Stiefvater   
41  23513349                                     Rupi Kaur   
42   9361589                              Erin Morgenstern   
43  18635016                                    Kiera Cass   
44  15749186                                     Jenny Han   
45  22489107                                 Marissa Meyer   
46     10964                                Diana Gabaldon   
47  10194157                                 Leigh Bardugo   
48  20698530                                     Jenny Han   
49  27833670                                  Blake Crouch   
50  22544764                                   Naomi Novik   
51     28187                                  Rick Riordan   
52  23164983                                  Ransom Riggs   
53  15839976                                  Pierce Brown   
54  25489625                              Ta-Nehisi Coates   
55  32075671                                  Angie Thomas   
56  28763485                                   Nicola Yoon   
57  22738563                      Chimamanda Ngozi Adichie   
58     13496                            George R.R. Martin   
59  25111004                                Colleen Hoover   
60   7171637                               Cassandra Clare   
61      1885                    Jane Austen, Anna Quindlen   
62      7613     George Orwell, Boris Grabnar, Peter Škerl   
63    186074                         

In [8]:
# получаем события для холодных пользователей и добавляем столбец avg_rating
cold_users_events_with_recs = (
    events_test[events_test["user_id"].isin(cold_users)]
    .merge(top_k_pop_items[["item_id", "avg_rating"]], on="item_id", how="left")
)

# находим индексы событий, где avg_rating не заполнен
cold_user_items_no_avg_rating_idx = cold_users_events_with_recs["avg_rating"].isnull()

# фильтруем события, где есть рекомендации
cold_user_recs = cold_users_events_with_recs[~cold_user_items_no_avg_rating_idx][["user_id", "item_id", "rating", "avg_rating"]]

# вычисляем долю событий, где рекомендации совпали по книгам
recommendation_match_ratio = 1 - cold_user_items_no_avg_rating_idx.mean()

# округляем ответ до сотых
recommendation_match_ratio_rounded = round(recommendation_match_ratio, 2)

print(recommendation_match_ratio_rounded)

0.2


In [9]:
# посчитаем метрики рекомендаций
rmse = mean_squared_error(cold_user_recs["rating"], cold_user_recs["avg_rating"], squared=False)
mae = mean_absolute_error(cold_user_recs["rating"], cold_user_recs["avg_rating"])

print(round(rmse, 2), round(mae, 2))

0.78 0.62


In [10]:
# посчитаем покрытие холодных пользователей рекомендациями

cold_users_hit_ratio = cold_users_events_with_recs.groupby("user_id").agg(hits=("avg_rating", lambda x: (~x.isnull()).mean()))

print(f"Доля пользователей без релевантных рекомендаций: {(cold_users_hit_ratio == 0).mean().iat[0]:.2f}")
print(f"Среднее покрытие пользователей: {cold_users_hit_ratio[cold_users_hit_ratio != 0].mean().iat[0]:.2f}")

Доля пользователей без релевантных рекомендаций: 0.59
Среднее покрытие пользователей: 0.44


# === Знакомство: первые персональные рекомендации

In [11]:
# используем Reader из библиотеки surprise для преобразования событий (events)
# в формат, необходимый surprise
reader = Reader(rating_scale=(1, 5))
surprise_train_set = Dataset.load_from_df(events_train[['user_id', 'item_id', 'rating']], reader)
surprise_train_set = surprise_train_set.build_full_trainset()

# инициализируем модель
svd_model = SVD(n_factors=100, random_state=0)

# обучаем модель
svd_model.fit(surprise_train_set) 

In [ ]:
surprise_test_set = list(events_test[['user_id', 'item_id', 'rating']].itertuples(index=False))

# получаем рекомендации для тестовой выборки
svd_predictions = svd_model.test(surprise_test_set)

In [15]:
rmse = accuracy.rmse(svd_predictions)
mae = accuracy.mae(svd_predictions)
                     
print(rmse, mae)

RMSE: 0.8289
MAE:  0.6474
0.8288711689059135 0.647437483750257


In [14]:
# инициализируем состояние генератора, это необходимо для получения
# одной и той же последовательности случайных чисел, только в учебных целях
np.random.seed(0)

random_model = NormalPredictor()

random_model.fit(surprise_train_set)
random_predictions = random_model.test(surprise_test_set)

In [16]:
rmse_random = accuracy.rmse(random_predictions)
mae_random = accuracy.mae(random_predictions)

RMSE: 1.2628
MAE:  1.0018


In [17]:
# вычисляем процентное отличие MAE для случайных рекомендаций от MAE для SVD
mae_difference_percentage = ((mae_random - mae) / mae) * 100

# округляем результат до целых
mae_difference_percentage_rounded = round(mae_difference_percentage)

print(mae_difference_percentage_rounded)

55


# Факультативное задание
## Матрица взаимодействий и первые персональные рекомендации

In [19]:
# Повторим разбиение на обучающую и тестовую выборки
train_test_global_time_split_date = pd.to_datetime("2017-08-01").date()
train_test_global_time_split_idx = events["started_at"] < train_test_global_time_split_date

events_train_filtered = events[train_test_global_time_split_idx]
events_test_filtered = events[~train_test_global_time_split_idx]

# Определим холодных пользователей
users_train_filtered = events_train_filtered["user_id"].drop_duplicates()
users_test_filtered = events_test_filtered["user_id"].drop_duplicates()
cold_users_filtered = users_test_filtered[~users_test_filtered.isin(users_train_filtered)]

# Найдем топ-100 наиболее популярных книг
top_pop_start_date = pd.to_datetime("2015-01-01").date()
item_popularity_filtered = events_train_filtered \
    .query("started_at >= @top_pop_start_date") \
    .groupby(["item_id"]).agg(users=("user_id", "nunique"), avg_rating=("rating", "mean")).reset_index()

scaler = MinMaxScaler()
item_popularity_filtered[["users_norm", "avg_rating_norm"]] = scaler.fit_transform(
    item_popularity_filtered[["users", "avg_rating"]]
)
item_popularity_filtered["popularity_score"] = (
    item_popularity_filtered["users_norm"] * item_popularity_filtered["avg_rating_norm"]
)
item_popularity_filtered = item_popularity_filtered.sort_values(by="popularity_score", ascending=False).reset_index(drop=True)
top_k_pop_items_filtered = item_popularity_filtered[item_popularity_filtered["avg_rating"] >= 4].head(100)

# Получим рекомендации для холодных пользователей
cold_users_events_with_recs_filtered = (
    events_test_filtered[events_test_filtered["user_id"].isin(cold_users_filtered)]
    .merge(top_k_pop_items_filtered[["item_id", "avg_rating"]], on="item_id", how="left")
)
cold_user_items_no_avg_rating_idx_filtered = cold_users_events_with_recs_filtered["avg_rating"].isnull()
cold_user_recs_filtered = cold_users_events_with_recs_filtered[~cold_user_items_no_avg_rating_idx_filtered][["user_id", "item_id", "rating", "avg_rating"]]

# Посчитаем метрики
rmse_filtered = mean_squared_error(cold_user_recs_filtered["rating"], cold_user_recs_filtered["avg_rating"], squared=False)
mae_filtered = mean_absolute_error(cold_user_recs_filtered["rating"], cold_user_recs_filtered["avg_rating"])

print(round(rmse_filtered, 2), round(mae_filtered, 2))

0.78 0.62


In [20]:
print("RMSE до фильтрации:", round(rmse, 2))
print("MAE до фильтрации:", round(mae, 2))
print("RMSE после фильтрации:", round(rmse_filtered, 2))
print("MAE после фильтрации:", round(mae_filtered, 2))

RMSE до фильтрации: 0.83
MAE до фильтрации: 0.65
RMSE после фильтрации: 0.78
MAE после фильтрации: 0.62


### Объяснение изменений
Улучшение метрик: Если метрики RMSE и MAE улучшились, это может быть связано с тем, что редкие айтемы создавали шум в данных. Удаление этих айтемов позволило модели лучше сосредоточиться на более популярных и репрезентативных айтемах.

Ухудшение метрик: Если метрики ухудшились, это может означать, что редкие айтемы все же содержали полезную информацию, которая помогала модели делать более точные предсказания. Возможно, эти айтемы были важны для определенной группы пользователей.

Стабильные метрики: Если метрики остались примерно на том же уровне, это может указывать на то, что редкие айтемы не оказывали значительного влияния на общую производительность модели.

Таким образом, удаление редких айтемов может как улучшить, так и ухудшить метрики в зависимости от конкретных данных и модели.

In [29]:
def get_recommendations_svd(user_id, all_items, events, model, include_seen=True, n=5):
    """Возвращает n рекомендаций для user_id"""

    # Получим список идентификаторов всех книг
    all_items = set(events['item_id'].unique())

    # Учитываем флаг, стоит ли уже прочитанные книги включать в рекомендации
    if include_seen:
        items_to_predict = list(all_items)
    else:
        # Получим список книг, которые пользователь уже прочитал ("видел")
        seen_items = set(events[events["user_id"] == user_id]['item_id'].unique())

        # Книги, которые пользователь ещё не читал
        # Только их и будем включать в рекомендации
        items_to_predict = list(all_items - seen_items)

    # Получаем скоры для списка книг, т. е. рекомендации
    predictions = [model.predict(user_id, item_id) for item_id in items_to_predict]

    # Сортируем рекомендации по убыванию скора и берём только n первых
    recommendations = sorted(predictions, key=lambda x: x.est, reverse=True)[:n]

    return pd.DataFrame([(pred.iid, pred.est) for pred in recommendations], columns=["item_id", "score"])

In [30]:
get_recommendations_svd(1296647, items, events_test, svd_model)

item_id  score
0  23602722      5
1  22037424      5
2   6309782      5
3  11295616      5
4  17332218      5

In [31]:
# выберем произвольного пользователя из тренировочной выборки ("прошлого")
user_id = events_train['user_id'].sample().iat[0]

print(f"user_id: {user_id}")

print("История (последние события, recent)")
user_history = (
    events_train
    .query("user_id == @user_id")
    .merge(items.set_index("item_id")[["author", "title", "genre_and_votes"]], on="item_id")
)
user_history_to_print = user_history[["author", "title", "started_at", "read_at", "rating", "genre_and_votes"]].tail(10)
display(user_history_to_print)

print("Рекомендации")
user_recommendations = get_recommendations_svd(user_id, items, events_train, svd_model)
user_recommendations = user_recommendations.merge(items[["item_id", "author", "title", "genre_and_votes"]], on="item_id")
display(user_recommendations)

user_id: 1087036
История (последние события, recent)


author  \
68                     Veronica Roth   
69         Gillian Flynn, В. Русанов   
70                      Kathy Reichs   
71                      Chelsea Cain   
72  Jussi Adler-Olsen, Lisa Hartford   
73                     Gillian Flynn   
74                Audrey Niffenegger   
75                      Kathy Reichs   
76                 Carolyn Parkhurst   
77                George R.R. Martin   

                                                title  started_at    read_at  \
68                          Divergent (Divergent, #1)  2014-06-02 2014-06-04   
69                                          Gone Girl  2014-05-27 2014-05-29   
70             Death du Jour (Temperance Brennan, #2)  2014-05-24 2014-05-27   
71  Heartsick (Archie Sheridan & Gretchen Lowell, #1)  2014-05-22 2014-05-22   
72       The Keeper of Lost Causes (Department Q, #1)  2014-05-30 2014-06-02   
73                                        Dark Places  2014-05-17 2014-05-22   
74                               Her Fearful Symmetry  2014-05-05 2014-05-08   
75                 Déjà Dead (Temperance Brennan, #1)  2014-05-13 2014-05-17   
76                                  The Dogs of Babel  2014-05-09 2014-05-10   
77  A Dance with Dragons (A Song of Ice and Fire, #5)  2014-05-04 2014-05-04   

    rating                                    genre_and_votes  
68       4  {'Young Adult': 20260, 'Science Fiction-Dystop...  
69       5  {'Fiction': 11773, 'Mystery': 9965, 'Thriller'...  
70       4  {'Mystery': 1206, 'Mystery-Crime': 579, 'Ficti...  
71       5  {'Mystery': 832, 'Thriller': 653, 'Fiction': 4...  
72       3  {'Mystery': 1225, 'Mystery-Crime': 627, 'Ficti...  
73       4  {'Mystery': 4534, 'Fiction': 4055, 'Thriller':...  
74       2  {'Fiction': 1984, 'Fantasy': 674, 'Fantasy-Par...  
75       4  {'Mystery': 2141, 'Fiction': 904, 'Mystery-Cri...  
76       5  {'Fiction': 522, 'Mystery': 102, 'Animals': 77...  
77       5  {'Fantasy': 22247, 'Fiction': 4512, 'Fantasy-E...

Рекомендации


item_id  score                                             author  \
0      2199      5                               Doris Kearns Goodwin   
1  16255632      5  David Gaider, Ben Gelinas, Mike Laidlaw, Dave ...   
2   2363958      5                                João Guimarães Rosa   
3  22552026      5                                     Jason Reynolds   
4  29237211      5                    Brian K. Vaughan, Fiona Staples   

                                               title  \
0  Team of Rivals: The Political Genius of Abraha...   
1           Dragon Age: The World of Thedas Volume 1   
2                             Grande Sertão: Veredas   
3                                      Long Way Down   
4                            Saga, Vol. 7 (Saga, #7)   

                                     genre_and_votes  
0  {'History': 4174, 'Nonfiction': 2127, 'Biograp...  
1  {'Fantasy': 134, 'Games-Video Games': 28, 'Art...  
2  {'Fiction': 85, 'Classics': 69, 'Cultural-Braz...  
3  {'Young Adult': 1871, 'Poetry': 1737, 'Contemp...  
4  {'Sequential Art-Graphic Novels': 2539, 'Seque...

# === Базовые подходы: коллаборативная фильтрация

In [33]:
# Перекодируем идентификаторы пользователей:
# из имеющихся в последовательность 0, 1, 2, ...
user_encoder = sklearn.preprocessing.LabelEncoder()
user_encoder.fit(events["user_id"])
events_train["user_id_enc"] = user_encoder.transform(events_train["user_id"])
events_test["user_id_enc"] = user_encoder.transform(events_test["user_id"])

# Перекодируем идентификаторы объектов:
# из имеющихся в последовательность 0, 1, 2, ...
item_encoder = sklearn.preprocessing.LabelEncoder()
item_encoder.fit(items["item_id"])
items["item_id_enc"] = item_encoder.transform(items["item_id"])

# Перекодируем идентификаторы объектов в событиях обучения и тестирования
events_train["item_id_enc"] = item_encoder.transform(events_train["item_id"])
events_test["item_id_enc"] = item_encoder.transform(events_test["item_id"])

# Определяем максимальное значение для events_train['item_id_enc']
max_item_id_enc = events_train['item_id_enc'].max()
print(f"Максимальное значение для events_train['item_id_enc']: {max_item_id_enc}")

/tmp/ipykernel_3065/2283926602.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  events_train["user_id_enc"] = user_encoder.transform(events_train["user_id"])
/tmp/ipykernel_3065/2283926602.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  events_test["user_id_enc"] = user_encoder.transform(events_test["user_id"])


Максимальное значение для events_train['item_id_enc']: 43304


/tmp/ipykernel_3065/2283926602.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  events_train["item_id_enc"] = item_encoder.transform(events_train["item_id"])
/tmp/ipykernel_3065/2283926602.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  events_test["item_id_enc"] = item_encoder.transform(events_test["item_id"])


In [36]:
n_users = events['user_id'].nunique()  # количество пользователей
n_items = events['item_id'].nunique()  # количество объектов

# Вычисляем общее количество элементов в матрице
total_elements = n_users * n_items

# Переводим в гигабайты
size_in_gb = total_elements / (1024 * 1024 * 1024)

# Отбрасываем дробную часть
size_in_gb_int = int(size_in_gb)

print(f"Количество уникальных пользователей: {n_users}")
print(f"Количество уникальных элементов (книг): {n_items}")
print(f"Размер матрицы в байтах: {total_elements}")
print(f"Размер матрицы в гигабайтах: {size_in_gb}")

Количество уникальных пользователей: 430585
Количество уникальных элементов (книг): 41673
Размер матрицы в байтах: 17943768705
Размер матрицы в гигабайтах: 16.71143686864525


In [37]:
# создаём sparse-матрицу формата CSR 
user_item_matrix_train = scipy.sparse.csr_matrix((
    events_train["rating"],
    (events_train['user_id_enc'], events_train['item_id_enc'])),
    dtype=np.int8) 

In [38]:
sum([sys.getsizeof(i) for i in user_item_matrix_train.data])/1024**3 

0.26370687410235405

In [39]:
als_model = AlternatingLeastSquares(factors=50, iterations=50, regularization=0.05, random_state=0)
als_model.fit(user_item_matrix_train)

/home/mle-user/sprint_4/lib/python3.10/site-packages/implicit/cpu/als.py:95: RuntimeWarning: OpenBLAS is configured to use 4 threads. It is highly recommended to disable its internal threadpool by setting the environment variable 'OPENBLAS_NUM_THREADS=1' or by calling 'threadpoolctl.threadpool_limits(1, "blas")'. Having OpenBLAS use a threadpool can lead to severe performance issues here.
  check_blas_config()
100%|██████████| 50/50 [02:49<00:00,  3.39s/it]


In [40]:
def get_recommendations_als(user_item_matrix, model, user_id, user_encoder, item_encoder, include_seen=True, n=5):
    """
    Возвращает отранжированные рекомендации для заданного пользователя
    """
    user_id_enc = user_encoder.transform([user_id])[0]
    recommendations = model.recommend(
         user_id_enc, 
         user_item_matrix[user_id_enc], 
         filter_already_liked_items=not include_seen,
         N=n)
    recommendations = pd.DataFrame({"item_id_enc": recommendations[0], "score": recommendations[1]})
    recommendations["item_id"] = item_encoder.inverse_transform(recommendations["item_id_enc"])
    
    return recommendations

# Факультативное задание

In [49]:
# Получаем список всех возможных user_id (перекодированных)
user_ids_encoded = range(len(user_encoder.classes_))

# Получаем рекомендации для всех пользователей
als_recommendations = als_model.recommend(
    user_ids_encoded,
    user_item_matrix_train[user_ids_encoded],
    filter_already_liked_items=False,
    N=100)

# Преобразуем полученные рекомендации в табличный формат
item_ids_enc = als_recommendations[0]
als_scores = als_recommendations[1]
als_recommendations = pd.DataFrame({
    "user_id_enc": np.repeat(user_ids_encoded, 100),
    "item_id_enc": item_ids_enc.flatten(),
    "score": als_scores.flatten()
})

# Приводим типы данных
als_recommendations["item_id_enc"] = als_recommendations["item_id_enc"].astype("int")
als_recommendations["score"] = als_recommendations["score"].astype("float")

# Получаем изначальные идентификаторы
als_recommendations["user_id"] = user_encoder.inverse_transform(als_recommendations["user_id_enc"])
als_recommendations["item_id"] = item_encoder.inverse_transform(als_recommendations["item_id_enc"])

# Удаляем промежуточные столбцы
als_recommendations = als_recommendations.drop(columns=["user_id_enc", "item_id_enc"])

# Сохраняем рекомендации в файл
als_recommendations.to_parquet("als_recommendations_new.parquet")


In [ ]:
# Функция для получения истории взаимодействий пользователя
def get_user_history(user_id, events_train, item_encoder):
    user_history = events_train[events_train['user_id'] == user_id]
    user_history['item_id_enc'] = item_encoder.transform(user_history['item_id'])
    return user_history

# Выбираем случайного пользователя
random_user_id = random.choice(user_encoder.classes_)

# Получаем рекомендации для случайного пользователя
user_recommendations = get_recommendations_als(user_item_matrix_train, als_model, random_user_id, user_encoder, item_encoder, include_seen=False, n=10)

# Получаем историю взаимодействий случайного пользователя
user_history = get_user_history(random_user_id, events_train, item_encoder)

# Добавляем информацию о книгах и авторах
books_info = pd.read_parquet("items.parquet")  # Предполагается, что у вас есть файл books.csv с информацией о книгах

# Объединяем историю и рекомендации с информацией о книгах
user_history = user_history.merge(books_info, on='item_id', how='left')
user_recommendations = user_recommendations.merge(books_info, on='item_id', how='left')

# Отображаем историю и рекомендации
print(f"История взаимодействий пользователя {random_user_id}:")
print(user_history[['item_id', 'title', 'author']])
print("\nРекомендации для пользователя:")
print(user_recommendations[['item_id', 'title', 'author', 'score']])

# Анализируем релевантность рекомендаций
seen_items = set(user_history['item_id'])
user_recommendations['seen'] = user_recommendations['item_id'].apply(lambda x: x in seen_items)
print("\nРекомендации с признаком seen:")
print(user_recommendations[['item_id', 'title', 'author', 'score', 'seen']])

# === Базовые подходы: контентные рекомендации

In [50]:
als_recommendations = (
    als_recommendations
    .merge(events_test[["user_id", "item_id", "rating"]]
               .rename(columns={"rating": "rating_test"}), 
           on=["user_id", "item_id"], how="left")
)

In [51]:
def compute_ndcg(rating: pd.Series, score: pd.Series, k):

    """ подсчёт ndcg
    rating: истинные оценки
    score: оценки модели
    k: количество айтемов (по убыванию score) для оценки, остальные - отбрасываются
    """
    
    # если кол-во объектов меньше 2, то NDCG - не определена
    if len(rating) < 2:
        return np.nan

    ndcg = sklearn.metrics.ndcg_score(np.asarray([rating.to_numpy()]), np.asarray([score.to_numpy()]), k=k)

    return ndcg

In [52]:
rating_test_idx = ~als_recommendations["rating_test"].isnull()
ndcg_at_5_scores = als_recommendations[rating_test_idx].groupby("user_id").apply(lambda x: compute_ndcg(x["rating_test"], x["score"], k=5))

In [53]:
print(ndcg_at_5_scores.mean()) 

0.975951794315703


### Факультативное задание

In [ ]:
# Функция для получения метрики NDCG
def calculate_ndcg(user_id, user_history, user_recommendations, k=5):
    # Получаем истинные релевантные оценки
    true_labels = user_history['item_id'].values

    # Получаем рекомендованные оценки
    recommended_items = user_recommendations['item_id'].values[:k]

    # Создаем массив релевантных оценок для рекомендованных элементов
    relevance = np.isin(recommended_items, true_labels).astype(int)

    # Считаем метрику NDCG
    ndcg = ndcg_score([relevance], [[1]*len(relevance)]) if len(relevance) > 0 else 0
    return ndcg

# Получаем список всех возможных user_id (перекодированных)
user_ids = user_encoder.classes_

# Инициализируем счетчик успешных вычислений NDCG
successful_ndcg_count = 0

# Проходим по каждому пользователю
for user_id in user_ids:
    # Получаем историю взаимодействий пользователя
    user_history = get_user_history(user_id, events_train, item_encoder)

    # Получаем рекомендации для пользователя
    user_recommendations = get_recommendations_als(user_item_matrix_train, als_model, user_id, user_encoder, item_encoder, include_seen=False, n=5)

    # Если у пользователя есть история и рекомендации
    if not user_history.empty and not user_recommendations.empty:
        # Считаем метрику NDCG
        ndcg = calculate_ndcg(user_id, user_history, user_recommendations)
        if ndcg > 0:
            successful_ndcg_count += 1

# Оцениваем долю пользователей, для которых удалось посчитать метрику NDCG
ndcg_success_ratio = successful_ndcg_count / len(user_ids)
print(f"Доля пользователей, для которых удалось посчитать метрику NDCG: {ndcg_success_ratio:.2f}")

/tmp/ipykernel_3065/3694335594.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_history['item_id_enc'] = item_encoder.transform(user_history['item_id'])
/tmp/ipykernel_3065/3694335594.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  user_history['item_id_enc'] = item_encoder.transform(user_history['item_id'])
/tmp/ipykernel_3065/3694335594.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See 

### I2I

In [ ]:
# Получаем похожие объекты для заданного объекта
similar_items = als_model.similar_items(item_id_enc)

# Преобразуем рекомендации в удобный формат
similar_items_df = pd.DataFrame(similar_items, columns=["item_id_enc", "similarity_score"])

# Получаем изначальные идентификаторы объектов
similar_items_df["item_id"] = item_encoder.inverse_transform(similar_items_df["item_id_enc"])

# Добавляем информацию о книгах
similar_items_df = similar_items_df.merge(books_info, on='item_id', how='left')

print(similar_items_df[['item_id', 'book_title', 'author_name', 'similarity_score']])

### U2U

In [ ]:
# Получаем похожих пользователей для заданного пользователя
similar_users = als_model.similar_users(user_id_enc)

# Преобразуем рекомендации в удобный формат
similar_users_df = pd.DataFrame(similar_users, columns=["user_id_enc", "similarity_score"])

# Получаем изначальные идентификаторы пользователей
similar_users_df["user_id"] = user_encoder.inverse_transform(similar_users_df["user_id_enc"])

print(similar_users_df[['user_id', 'similarity_score']])

# === Базовые подходы: валидация

# === Двухстадийный подход: метрики

# === Двухстадийный подход: 

# === Двухстадийный подход: модель

# === Двухстадийный подход: построение признаков